In [ ]:
%matplotlib inline
import numpy as np
import matplotlib.pyplot as plt
from setupFigure import SetupFigure

In [ ]:
def dft_coeff(x):
    """
    Evaluate c_n = 1/N*sum_{k=0}^{N-1}x_k exp(-i*2*pi*nk/N)
    :param x: samples of function with length N
    """
    ns = np.size(x)
    c = np.zeros(ns, dtype=np.complex64)  # zero coefficients before summing
    for n in range(ns):
        for k in range(ns):
            arg = -2*np.pi*1j*n*k/ns
            c[n] = c[n]+x[k]*np.exp(arg)
        c[n] = c[n]/ns
    return c

In [ ]:
def dft_inverse(c):
    """
    Evaluate x_k = sum_{n=0}^{N-1}c_n exp(i*2*pi*nk/N)
    :param c: complex DFT coefficients
    """
    ns = np.size(c)
    x = np.zeros(ns)   # zero values before summing
    for k in range(ns):
        for n in range(ns):
            arg = +2*np.pi*1j*n*k/ns
            x[k] = x[k]+np.real(c[n]*np.exp(arg))   # since x[k] is real, we only sum the real parts
    return x

In [ ]:
def dft_inverse_any_time(c, period, dt, nt, mc=1):
    """
    Evaluate x(k*dt) = sum_{n=0}^{N-1}c_n exp(i*2*pi*n*(k*dt)/T)
    :param c: complex DFT coefficients
    :param period: period of time series
    :param dt: new time sampling interval
    :param nt: number of time samples
    :param mc: take mc*N Fourier coefficients
    """
    ns = np.size(c)
    x = np.zeros(nt)
    for k in range(nt):
        for n in range(mc*ns):
            arg = +2*np.pi*1j*n*(k*dt)/period
            dum, n2 = divmod(n,ns)                   # use periodicity c[n+N] = c[n]
            x[k] = x[k]+np.real(c[n2]*np.exp(arg))   # since x[k] result is real, we only sum the real parts
    return x

### The sampled Gaussian function

Setup of Gaussian function $x(t)=\exp(-(t-3)^2)$ in range $0 < t < 6$. We take $\Delta t=0.1$ producing 60 intervals and N=61 samples.
Note that the period of the function is then $T=N\Delta t=6.1$ and not $6.0$; hence $x(T=N\Delta t) = x(0)$.

In [ ]:
tmax = 6.0
dt = 0.1
ns = int(tmax/dt)+1
period = ns*dt
x = np.zeros(ns)
t = np.linspace(0, tmax, ns)

In [ ]:
x = np.exp(-(t-3)**2)   # compute ns samples of Gaussian

In [ ]:
fig1, ax1 = SetupFigure(10, 5, "Time [s]", "x(t)", "Gaussian, DT=0.1, TMAX=6", 14)
ax1.plot(t, x, color='blue', ls=':', marker='o', markersize=4.0)

### The Fourier coefficients of the sampled Gaussian

Compute the Fourier coefficients using $c_n = \frac{1}{N}\sum\limits_{k=0}^{N-1} x_k \exp(-2\pi i nk/N)$. The frequencies to $c_n$ are $f_n = n/T$ or $\omega_n = 2\pi n/T$. The frequency to $c_{N-1}$ is $\frac{N-1}{T}$.

In [ ]:
c = dft_coeff(x)
f = np.linspace(0, (ns-1)/period, ns)

In [ ]:
fig2, ax2 = SetupFigure(10, 5, "Frequency [Hz]", "c_n", "Fourier coefficients of Gaussian, DT=0.1, TMAX=6", 14)
ax2.plot(f, np.absolute(c), color='black', ls='--', marker='d', label='abs')
ax2.plot(f, np.real(c), color='red', ls=':', marker='*', markersize=4.0, label='real')
ax2.plot(f, np.imag(c), color='blue', ls=':', marker='o', markersize=4.0, label='imag')
ax2.legend()

### The recovered Gaussian at the original samples

Recover the samples by inverse discrete Fourier transform: $x_k = \sum\limits_{n=0}^{N-1} c_n \exp(2\pi i nk/N)$ belonging to times $t_k=k\Delta t$.

In [ ]:
xr = dft_inverse(c)

In [ ]:
fig3, ax3 = SetupFigure(10, 5, "Time [s]", "xr(t)", "Recovered Gaussian, DT=0.1, TMAX=6", 14)
ax3.plot(t, xr , color='blue', ls='--',  marker='o', markersize=4.0)

### The recovered Gaussian at original sampling interval up to TMAX=12

Evaluate the inverse transform at times beyond $T$ using $x_k = \sum\limits_{n=0}^{N-1} c_n \exp(2\pi in t/T)$. Here, we take the same sampling interval but extend the time range to $12$. We get a periodic continuation of the Gaussian.

In [ ]:
tmax = 12
nt = int(tmax/dt)+1
tlong = np.linspace(0, tmax, nt)
xrlong = dft_inverse_any_time(c, period, dt, nt)

In [ ]:
fig4, ax4 = SetupFigure(10, 5, "Time [s]", "xrlong(t)", "Recovered Gaussian, DT=0.1, TMAX=12", 14)
ax4.plot(tlong, xrlong , color='blue', ls='--',  marker='o', markersize=4.0)

### The recovered Gausian with dense sampling (DT=0.01)

Here, we also evaluate the Fourier series for times in between the original samples by choosing times $t=0.1\,k\Delta t$. Evidently, this is not a suitable interpolation method.

In [ ]:
tmax = 6
dtnew = 0.1*dt
nt = int(tmax/dtnew)+1
tdense = np.linspace(0, tmax, nt)
xdense = dft_inverse_any_time(c, period, dtnew, nt, mc=1)        # dense sampling

In [ ]:
fig5, ax5 = SetupFigure(10, 5, "Time [s]", "xrdense(t)", "Recovered Gaussian, DT=0.01, TMAX=6", 14)
ax5.plot(tdense, xdense , color='blue', ls=':',  marker='o', markersize=4.0)
ax5.plot(t, x , color='red', ls='--',  marker='d', markersize=4.0)

### The recovered Gausian with dense sampling and high order Fourier coefficients (DT=0.01, mc*N-1)

 Here, we again use dense sampling and, in addition, sum up the coefficients to $mc*N-1$ thus introducing higher frequencies. By doing this, we aproximate the time function $x(t)=\sum_{k=0}^{N-1} x_k\delta(t-k\Delta t)$ with high peaks at the samples and zero values in between. Play with increasingly higher values of $mc$.

In [ ]:
xhigh = dft_inverse_any_time(c, period, dtnew, nt, mc=10)         # dense sampling and higher freqeuncies

In [ ]:
fig6, ax6 = SetupFigure(10, 5, "Time [s]", "xrhigh(t)", "Recovered Gaussian, DT=0.01, TMAX=6, high frequencies", 14)
ax6.plot(tdense, xhigh , color='blue', ls=':',  marker='o', markersize=4.0)